d-sandbox

<div style="text-align: center; line-height: 0; padding-top: 9px;">
  <img src="https://databricks.com/wp-content/uploads/2018/03/db-academy-rgb-1200px.png" alt="Databricks Learning" style="width: 600px">
</div>

-sandbox
# Capstone Project: 3 Production Deployments

The goal of this project is to deploy a trained machine learning model into production using all three deployment paradigms: batch, streaming, and REST.  An optional exercise entails creating a monitoring and alerting infrastructure.

## ![Spark Logo Tiny](https://files.training.databricks.com/images/105/logo_spark_tiny.png) In this capstone you:<br>
 - Apply a model trained in `sklearn` across a Spark DataFrame
 - Perform predictions on an incoming stream of data
 - Deploy a rest endpoint
 - _Optional:_ Create a monitoring and alerting solution
 
<img alt="Caution" title="Caution" style="vertical-align: text-bottom; position: relative; height:1.3em; top:0.0em" src="https://files.training.databricks.com/static/images/icon-warning.svg"/> **Please be sure to delete any infrastructure you build after the course so you don't incur unexpected expenses.**

In [0]:
%run "./Includes/Classroom-Setup"

Preparing the learning environment...

Defining courseware-specific utility methods...

Mounting course-specific datasets to /mnt/training ... Datasets are already mounted to /mnt/training from s3a://databricks-corp-training/common

All done!

Define a name for the stream to be used later in this lesson.

In [0]:
myStreamName = "capstone_pi"

Import the AirBnB dataset.  Create the following objects:<br><br>

* `pandasDF`: a Pandas DataFrame of all the data
* `pandasX`: a Pandas DataFrame of the `X` values
* `pandasy`: a Pandas DataFrame of the `y` values
* `sparkDF`: a Spark DataFrame of all the data

In [0]:
import pandas as pd
from sklearn.model_selection import train_test_split

# pandasDF = pd.read_csv("/dbfs/mnt/training/airbnb/sf-listings/airbnb-cleaned-mlflow.csv")
pandasDF = pd.read_csv("https://raw.githubusercontent.com/bernhard-42/mlflow-experiments/master/data/airbnb-cleaned-mlflow.csv")
pandasX = pandasDF.drop(["price"], axis=1)
pandasy = pandasDF["price"]

sparkDF = spark.createDataFrame(pandasDF)
display(sparkDF)

host_total_listings_count neighbourhood_cleansed zipcode latitude longitude property_type room_type accommodates bathrooms bedrooms beds bed_type minimum_nights number_of_reviews review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value price 1.0 0 0 37.769310377340766 -122.43385634489 0 0 3.0 1.0 1.0 2.0 0 1.0 127.0 97.0 10.0 10.0 10.0 10.0 10.0 10.0 170.0 2.0 1 1 37.745112331410034 -122.42101788836888 0 0 5.0 1.0 2.0 3.0 0 30.0 112.0 98.0 10.0 10.0 10.0 10.0 10.0 9.0 235.0 10.0 2 0 37.766689597862175 -122.45250461761628 0 1 2.0 4.0 1.0 1.0 0 32.0 17.0 85.0 8.0 8.0 9.0 9.0 9.0 8.0 65.0 4.0 3 2 37.73074592978503 -122.44840862635226 1 1 1.0 2.0 1.0 1.0 0 3.0 76.0 95.0 9.0 9.0 10.0 10.0 9.0 9.0 60.0 10.0 2 0 37.76487219421756 -122.45182799146508 1 1 2.0 4.0 1.0 1.0 0 32.0 7.0 91.0 9.0 9.0 9.0 9.0 9.0 9.0 65.0 2.0 0 0 37.77524858589268 -122.43637374831292 1 0 5.0 1.5 2.0 2.0 0 5.0 26.0 97.0 10.0 10.0 10.0 10.0 10.0 10.0 575.0 1.0 0 3 37.78470745496073 -122.44555431261594 0 0 7.0 1.0 2.0 1.0 0 2.0 27.0 88.0 9.0 7.0 10.0 10.0 9.0 9.0 255.0 2.0 4 1 37.75918889708064 -122.42236687240562 0 1 3.0 1.0 1.0 2.0 0 1.0 559.0 98.0 10.0 10.0 10.0 10.0 10.0 9.0 139.0 1.0 4 1 37.75174004606522 -122.4094205953428 0 0 4.0 2.5 3.0 3.0 0 3.0 24.0 95.0 9.0 9.0 10.0 10.0 9.0 9.0 285.0 1.0 5 4 37.76258885144137 -122.40543055237004 1 1 2.0 1.0 1.0 1.0 0 1.0 386.0 93.0 9.0 9.0 10.0 10.0 9.0 9.0 135.0 1.0 4 1 37.75874294929672 -122.4132720164374 1 0 6.0 1.0 2.0 3.0 0 3.0 274.0 95.0 10.0 10.0 10.0 9.0 9.0 9.0 265.0 46.0 6 5 37.78573889680189 -122.40797710199776 0 0 2.0 1.5 1.0 1.0 0 30.0 16.0 91.0 10.0 9.0 10.0 10.0 10.0 9.0 139.0 10.0 2 0 37.77018946066375 -122.44594218370484 0 1 1.0 4.0 1.0 2.0 0 32.0 5.0 75.0 8.0 8.0 9.0 10.0 9.0 7.0 85.0 10.0 2 0 37.76894262424544 -122.44778223886064 1 1 2.0 3.0 1.0 2.0 0 32.0 5.0 64.0 6.0 6.0 10.0 9.0 9.0 8.0 85.0 1.0 7 6 37.76074548179248 -122.4303240593966 0 1 1.0 1.0 1.0 1.0 0 3.0 353.0 98.0 10.0 10.0 10.0 10.0 10.0 10.0 79.0 1.0 4 1 37.75490669862631 -122.42245501922534 0 0 3.0 1.0 1.0 2.0 0 3.0 83.0 98.0 10.0 10.0 10.0 10.0 10.0 9.0 215.0 3.0 0 0 37.77252151838996 -122.43215647138362 2 1 2.0 1.0 1.0 1.0 0 2.0 297.0 98.0 10.0 10.0 10.0 10.0 10.0 10.0 110.0 1.0 4 1 37.76348966609621 -122.41517400287556 3 1 2.0 1.0 0.0 1.0 0 3.0 215.0 96.0 10.0 10.0 10.0 10.0 9.0 9.0 188.0 10.0 2 0 37.76480029761001 -122.4525132294276 1 1 2.0 4.0 1.0 1.0 0 32.0 14.0 78.0 8.0 8.0 10.0 10.0 10.0 7.0 65.0 1.0 4 1 37.75065032945569 -122.41983820914383 0 0 5.0 1.0 2.0 4.0 0 1.0 75.0 96.0 10.0 10.0 10.0 10.0 10.0 9.0 225.0 2.0 1 1 37.74556318786063 -122.41206808320705 0 1 2.0 0.5 1.0 1.0 0 3.0 204.0 98.0 10.0 10.0 10.0 10.0 9.0 10.0 95.0 1.0 7 6 37.75963016394613 -122.4414323272976 4 0 2.0 1.0 1.0 1.0 0 3.0 301.0 97.0 10.0 10.0 10.0 10.0 10.0 10.0 155.0 2.0 5 4 37.75644595380928 -122.39910232220872 2 1 2.0 1.0 1.0 1.0 0 2.0 232.0 97.0 10.0 10.0 10.0 10.0 10.0 10.0 155.0 1.0 2 0 37.77161759839722 -122.4383620129092 0 1 1.0 1.0 1.0 1.0 0 1.0 153.0 95.0 10.0 9.0 10.0 10.0 10.0 9.0 79.0 2.0 0 3 37.78716464559002 -122.43386112927004 0 0 4.0 1.0 1.0 2.0 0 2.0 225.0 95.0 10.0 10.0 10.0 10.0 10.0 10.0 195.0 1.0 8 7 37.741876130512445 -122.43121541816402 1 1 2.0 1.0 1.0 1.0 0 5.0 11.0 100.0 10.0 10.0 10.0 10.0 10.0 10.0 150.0 3.0 0 0 37.77728949301072 -122.43421149153566 2 1 2.0 1.0 1.0 1.0 0 2.0 343.0 98.0 10.0 10.0 10.0 10.0 10.0 10.0 110.0 1.0 5 4 37.76212201623429 -122.39540903672584 1 1 3.0 1.0 0.0 1.0 0 4.0 265.0 95.0 9.0 10.0 10.0 10.0 10.0 9.0 125.0 3.0 0 3 37.78894736246063 -122.43030637005006 1 1 2.0 1.0 1.0 1.0 0 2.0 52.0 90.0 9.0 9.0 10.0 9.0 10.0 9.0 110.0 3.0 0 0 37.77477848177087 -122.43149873605402 0 0 10.0 2.0 4.0 7.0 0 4.0 26.0 89.0 9.0 8.0 8.0 9.0 9.0 9.0 393.0 1.0 7 6 37.76297967565378 -122.43136441227804 0 0 2.0 1.0 1.0 1.0 0 30.0 128.0 100.0 10.0 10.0 10.0 10.0 10.0 10.0 175.0 2.0 4 1 37.76097556330237 -122.4215807919612 

-sandbox
Train an AdaBoost regressor.  AdaBoost is meta-estimator that works by fitting one regressor to a dataset and then fits many additional copies of that same regressor to the dataset but with different weights for different errors.

<img alt="Side Note" title="Side Note" style="vertical-align: text-bottom; position: relative; height:1.75em; top:0.05em; transform:rotate(15deg)" src="https://files.training.databricks.com/static/images/icon-note.webp"/> Knowing how this algorithm works is not necessary for this capstone.  To deploy a model, we just need to know its inputs and outputs.  To read more about AdaBoost, <a href="https://scikit-learn.org/stable/modules/generated/sklearn.ensemble.AdaBoostRegressor.html#sklearn.ensemble.AdaBoostRegressor" target="_blank">see the `sklearn` documentation.</a>

In [0]:
from sklearn.ensemble import AdaBoostRegressor, RandomForestRegressor
from sklearn.metrics import mean_squared_error

seed = 42

rf = RandomForestRegressor(n_estimators=100, max_depth=4, random_state=seed)
ada = AdaBoostRegressor(base_estimator=rf, n_estimators=400)
ada.fit(pandasX, pandasy)

predictions = pandasX.copy()
predictions["prediction"] = ada.predict(pandasX)

mse = mean_squared_error(pandasy, predictions["prediction"]) # This is on the same data the model was trained

In [0]:
print(mse)

### Apply a model trained in `sklearn` across a Spark DataFrame

Perform the following steps to apply the AdaBoost model to a Spark DataFrame:<br><br>

1. Log the model `ada` and evaluation metric `mse` using `mlflow`
2. Create a Spark UDF from this logged model
3. Apply the UDF to `sparkDF` (you may have to drop columns)

In [0]:
# ANSWER
import mlflow.sklearn

with mlflow.start_run(run_name="Final RF Model") as run: 
  mlflow.sklearn.log_model(ada, "adaboost-model")
  mlflow.log_metric("Train data MSE", mse)
  
  run_info = run.info

2023/07/26 12:21:32 WARNING mlflow.models.model: Model logged without a signature. Signatures will be required for upcoming model registry features as they validate model inputs and denote the expected schema of model outputs. Please visit https://www.mlflow.org/docs/2.5.0/models.html#set-signature-on-logged-model for instructions on setting a model signature on your logged model.
/databricks/python/lib/python3.9/site-packages/_distutils_hack/__init__.py:30: UserWarning: Setuptools is replacing distutils.
  warnings.warn("Setuptools is replacing distutils.")


In [0]:
# ANSWER
predict = mlflow.pyfunc.spark_udf(spark, run_info.artifact_uri + "/adaboost-model")

2023/07/26 12:21:41 WARNING mlflow.pyfunc: Calling `spark_udf()` with `env_manager="local"` does not recreate the same environment that was used during training, which may lead to errors or inaccurate predictions. We recommend specifying `env_manager="conda"`, which automatically recreates the environment that was used to train the model and performs inference in the recreated environment.
2023/07/26 12:21:41 INFO mlflow.models.flavor_backend_registry: Selected backend for flavor 'python_function'
2023/07/26 12:21:41 WARNING mlflow.pyfunc: No 'result_type' provided for spark_udf and the model does not have an output schema. 'result_type' is set to 'double' type.


In [0]:
# ANSWER
predictionDF = (sparkDF
  .withColumn("prediction", predict(*sparkDF.drop("price").columns))
)

display(predictionDF)

host_total_listings_count neighbourhood_cleansed zipcode latitude longitude property_type room_type accommodates bathrooms bedrooms beds bed_type minimum_nights number_of_reviews review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value price prediction 1.0 0 0 37.769310377340766 -122.43385634489 0 0 3.0 1.0 1.0 2.0 0 1.0 127.0 97.0 10.0 10.0 10.0 10.0 10.0 10.0 170.0 185.31464233343476 2.0 1 1 37.745112331410034 -122.42101788836888 0 0 5.0 1.0 2.0 3.0 0 30.0 112.0 98.0 10.0 10.0 10.0 10.0 10.0 9.0 235.0 259.93110583884925 10.0 2 0 37.766689597862175 -122.45250461761628 0 1 2.0 4.0 1.0 1.0 0 32.0 17.0 85.0 8.0 8.0 9.0 9.0 9.0 8.0 65.0 119.74435827287391 4.0 3 2 37.73074592978503 -122.44840862635226 1 1 1.0 2.0 1.0 1.0 0 3.0 76.0 95.0 9.0 9.0 10.0 10.0 9.0 9.0 60.0 117.90281418587124 10.0 2 0 37.76487219421756 -122.45182799146508 1 1 2.0 4.0 1.0 1.0 0 32.0 7.0 91.0 9.0 9.0 9.0 9.0 9.0 9.0 65.0 125.75259032365925 2.0 0 0 37.77524858589268 -122.43637374831292 1 0 5.0 1.5 2.0 2.0 0 5.0 26.0 97.0 10.0 10.0 10.0 10.0 10.0 10.0 575.0 389.96882590902607 1.0 0 3 37.78470745496073 -122.44555431261594 0 0 7.0 1.0 2.0 1.0 0 2.0 27.0 88.0 9.0 7.0 10.0 10.0 9.0 9.0 255.0 316.455310339529 2.0 4 1 37.75918889708064 -122.42236687240562 0 1 3.0 1.0 1.0 2.0 0 1.0 559.0 98.0 10.0 10.0 10.0 10.0 10.0 9.0 139.0 126.67749673566634 1.0 4 1 37.75174004606522 -122.4094205953428 0 0 4.0 2.5 3.0 3.0 0 3.0 24.0 95.0 9.0 9.0 10.0 10.0 9.0 9.0 285.0 412.7334329619083 1.0 5 4 37.76258885144137 -122.40543055237004 1 1 2.0 1.0 1.0 1.0 0 1.0 386.0 93.0 9.0 9.0 10.0 10.0 9.0 9.0 135.0 125.64278640209062 1.0 4 1 37.75874294929672 -122.4132720164374 1 0 6.0 1.0 2.0 3.0 0 3.0 274.0 95.0 10.0 10.0 10.0 9.0 9.0 9.0 265.0 303.4821343283494 46.0 6 5 37.78573889680189 -122.40797710199776 0 0 2.0 1.5 1.0 1.0 0 30.0 16.0 91.0 10.0 9.0 10.0 10.0 10.0 9.0 139.0 186.83795785825407 10.0 2 0 37.77018946066375 -122.44594218370484 0 1 1.0 4.0 1.0 2.0 0 32.0 5.0 75.0 8.0 8.0 9.0 10.0 9.0 7.0 85.0 199.7249619063633 10.0 2 0 37.76894262424544 -122.44778223886064 1 1 2.0 3.0 1.0 2.0 0 32.0 5.0 64.0 6.0 6.0 10.0 9.0 9.0 8.0 85.0 185.83329523969667 1.0 7 6 37.76074548179248 -122.4303240593966 0 1 1.0 1.0 1.0 1.0 0 3.0 353.0 98.0 10.0 10.0 10.0 10.0 10.0 10.0 79.0 126.67749673566634 1.0 4 1 37.75490669862631 -122.42245501922534 0 0 3.0 1.0 1.0 2.0 0 3.0 83.0 98.0 10.0 10.0 10.0 10.0 10.0 9.0 215.0 170.6133243200519 3.0 0 0 37.77252151838996 -122.43215647138362 2 1 2.0 1.0 1.0 1.0 0 2.0 297.0 98.0 10.0 10.0 10.0 10.0 10.0 10.0 110.0 127.75051341521164 1.0 4 1 37.76348966609621 -122.41517400287556 3 1 2.0 1.0 0.0 1.0 0 3.0 215.0 96.0 10.0 10.0 10.0 10.0 9.0 9.0 188.0 125.64278640209062 10.0 2 0 37.76480029761001 -122.4525132294276 1 1 2.0 4.0 1.0 1.0 0 32.0 14.0 78.0 8.0 8.0 10.0 10.0 10.0 7.0 65.0 140.9251858604896 1.0 4 1 37.75065032945569 -122.41983820914383 0 0 5.0 1.0 2.0 4.0 0 1.0 75.0 96.0 10.0 10.0 10.0 10.0 10.0 9.0 225.0 258.63991704591785 2.0 1 1 37.74556318786063 -122.41206808320705 0 1 2.0 0.5 1.0 1.0 0 3.0 204.0 98.0 10.0 10.0 10.0 10.0 9.0 10.0 95.0 122.88604398861901 1.0 7 6 37.75963016394613 -122.4414323272976 4 0 2.0 1.0 1.0 1.0 0 3.0 301.0 97.0 10.0 10.0 10.0 10.0 10.0 10.0 155.0 185.31464233343476 2.0 5 4 37.75644595380928 -122.39910232220872 2 1 2.0 1.0 1.0 1.0 0 2.0 232.0 97.0 10.0 10.0 10.0 10.0 10.0 10.0 155.0 123.92075432219471 1.0 2 0 37.77161759839722 -122.4383620129092 0 1 1.0 1.0 1.0 1.0 0 1.0 153.0 95.0 10.0 9.0 10.0 10.0 10.0 9.0 79.0 127.40593931745374 2.0 0 3 37.78716464559002 -122.43386112927004 0 0 4.0 1.0 1.0 2.0 0 2.0 225.0 95.0 10.0 10.0 10.0 10.0 10.0 10.0 195.0 241.9071899188615 1.0 8 7 37.741876130512445 -122.43121541816402 1 1 2.0 1.0 1.0 1.0 0 5.0 11.0 100.0 10.0 10.0 10.0 10.0 10.0 10.0 150.0 120.4923043406116 3.0 0 0 37.77728949301072 -122.43421149153566 2 1 2.0 1.0 1.0 1.0 0 2.0 343.0 98.0 10.0 10.0 10.0 10.0 10.0 10.0 110.0 127.7505134152

### Perform predictions on an incoming stream of data

Perform the following steps to apply the AdaBoost model to a stream of incoming data:<br><br>

1. Run the logic defined for you to create the schema and stream
2. Apply the UDF to `sparkDF` defined above to the stream
3. Write the results to a delta table

In [0]:
from pyspark.sql.types import DoubleType, IntegerType, StructType

schema = (StructType()
  .add("host_total_listings_count", DoubleType())
  .add("neighbourhood_cleansed", IntegerType())
  .add("zipcode", IntegerType())
  .add("latitude", DoubleType())
  .add("longitude", DoubleType())
  .add("property_type", IntegerType())
  .add("room_type", IntegerType())
  .add("accommodates", DoubleType())
  .add("bathrooms", DoubleType())
  .add("bedrooms", DoubleType())
  .add("beds", DoubleType())
  .add("bed_type", IntegerType())
  .add("minimum_nights", DoubleType())
  .add("number_of_reviews", DoubleType())
  .add("review_scores_rating", DoubleType())
  .add("review_scores_accuracy", DoubleType())
  .add("review_scores_cleanliness", DoubleType())
  .add("review_scores_checkin", DoubleType())
  .add("review_scores_communication", DoubleType())
  .add("review_scores_location", DoubleType())
  .add("review_scores_value", DoubleType())
  .add("price", DoubleType())
)

spark.conf.set("spark.sql.shuffle.partitions", "8")
streamingData = (spark
  .readStream
  .schema(schema)
  .option("maxFilesPerTrigger", 1)
  .parquet("/mnt/training/airbnb/sf-listings/airbnb-cleaned-mlflow.parquet/")
)

In [0]:
# ANSWER
predictionsDF = streamingData.withColumn("prediction", predict(*streamingData.drop("price").columns))

# Preview our stream - you must stop the stream before resuming
display(predictionsDF, streamName = myStreamName)

---------------------------------------------------------------------------
IllegalArgumentException                  Traceback (most recent call last)
File <command-3761410829409792>:5
      2 predictionsDF = streamingData.withColumn("prediction", predict(*streamingData.drop("price").columns))
      4 # Preview our stream - you must stop the stream before resuming
----> 5 display(predictionsDF, streamName = myStreamName)

File /databricks/python_shell/dbruntime/display.py:76, in Display.display(self, input, *args, **kwargs)
     74 elif isinstance(input, DataFrame):
     75     if hasattr(input, "isStreaming") and input.isStreaming:
---> 76         handleStreamingDataFrame(input, self.sc, self.sqlContext, self.entry_point, kwargs)
     77     else:
     78         if kwargs.get('streamName'):

File /databricks/python_shell/dbruntime/display.py:122, in handleStreamingDataFrame(input, sc, sqlContext, entry_point, kwargs)
    117     trigger = None
    119 name = kwargs.get('streamName',

In [0]:
# Wait until the stream is ready for processing
untilStreamIsReady(myStreamName)

The stream is active and ready.


In [0]:
# Stop the stream once you are done previewing it
# and before moving on to the next step...
stopAllStreams()

Stopping capstone_pi


In [0]:
# Delete any files that might exist from previous runs
dbutils.fs.rm(workingDir + "ml-deployment-capstone", True)

# Write the results to a delta table location identified by:
writePath = workingDir + "/ml-deployment-capstone/predictions"

# Make sure to specify the following checkpoint-location as identified by:
checkpointLocation = workingDir + "/ml-deployment-capstone/stream.checkpoint"

In [0]:
workingDir

Out[17]: 'dbfs:/user/laurent.raffalli@laposte.net/ml_deployment/09_capstone_project'

In [0]:
# ANSWER
(predictionsDF
  .writeStream                                      # Write the stream
  .queryName(myStreamName)                          # Name the stream
  .format("delta")                                  # Use the delta format
  .partitionBy("zipcode")                           # Specify a feature to partition on
  .option("checkpointLocation", checkpointLocation) # Specify where to log metadata
  .option("path", writePath)                        # Specify the output path
  .outputMode("append")                             # Append new records to the output path
  .start()                                          # Start the operation
)

Out[18]: <pyspark.sql.streaming.query.StreamingQuery at 0x7f2e4c6f4760>

In [0]:
# Wait until the stream is ready for processing
untilStreamIsReady(myStreamName)

Check to see if your files are there

In [0]:
from pyspark.sql.utils import AnalysisException

try:
  print(spark.read.format("delta").load(writePath).count())
except AnalysisException:
  print("Files not found.  This could be because the stream hasn't initialized.  Try again in a moment.")

Files not found.  This could be because the stream hasn't initialized.  Try again in a moment.


In [0]:
display(spark.read.format("delta").load(writePath))

host_total_listings_count neighbourhood_cleansed zipcode latitude longitude property_type room_type accommodates bathrooms bedrooms beds bed_type minimum_nights number_of_reviews review_scores_rating review_scores_accuracy review_scores_cleanliness review_scores_checkin review_scores_communication review_scores_location review_scores_value price prediction 3.0 8 1 37.747362709305264 -122.42489529846125 6 1 2.0 1.5 1.0 1.0 0 1.0 24.0 100.0 10.0 10.0 10.0 10.0 10.0 10.0 125.0 124.57084245655116 1.0 1 1 37.73330121656639 -122.41979720416167 1 0 6.0 2.0 3.0 3.0 0 3.0 3.0 100.0 10.0 10.0 10.0 10.0 9.0 10.0 357.0 399.18438907341806 1.0 4 1 37.75013920397615 -122.40964224773603 1 1 2.0 1.0 1.0 1.0 0 5.0 5.0 100.0 10.0 10.0 10.0 10.0 9.0 10.0 59.0 122.88604398861901 2.0 1 1 37.7453003422857 -122.42133197701133 6 0 4.0 1.0 2.0 2.0 0 3.0 2.0 100.0 10.0 10.0 10.0 10.0 10.0 9.0 250.0 321.42086693936955 1.0 4 1 37.754655433516795 -122.41197151919526 1 0 8.0 1.0 4.0 4.0 0 3.0 28.0 99.0 10.0 10.0 10.0 10.0 10.0 10.0 445.0 393.64156481572866 1.0 4 1 37.75488403376368 -122.40769956788749 13 0 2.0 1.0 0.0 1.0 0 3.0 80.0 95.0 10.0 10.0 10.0 10.0 10.0 9.0 125.0 185.36494409302435 4.0 1 1 37.741816830020355 -122.40895657437218 1 1 2.0 2.0 1.0 2.0 3 30.0 4.0 100.0 10.0 10.0 10.0 10.0 10.0 10.0 120.0 123.92075432219471 1.0 4 1 37.76221601240075 -122.42332215339168 0 0 4.0 1.0 1.0 3.0 0 2.0 84.0 97.0 10.0 10.0 10.0 10.0 10.0 10.0 240.0 243.1750587200811 1.0 4 1 37.7614820537443 -122.40925392305105 0 0 2.0 1.0 1.0 1.0 0 1.0 39.0 98.0 10.0 10.0 10.0 10.0 10.0 9.0 200.0 185.31464233343476 3.0 4 1 37.761718866629494 -122.42348307335551 0 1 2.0 1.0 1.0 1.0 0 1.0 31.0 99.0 10.0 10.0 10.0 10.0 10.0 10.0 155.0 126.67749673566634 3.0 4 1 37.74874493352542 -122.41824907236744 0 1 2.0 1.0 1.0 2.0 0 14.0 104.0 97.0 10.0 10.0 10.0 10.0 10.0 10.0 85.0 123.92075432219471 3.0 7 1 37.759842162136955 -122.42639053748486 0 0 5.0 1.0 3.0 3.0 0 3.0 4.0 95.0 10.0 10.0 10.0 10.0 10.0 9.0 325.0 336.16342457834355 1.0 4 1 37.7599551383521 -122.42410641814496 1 0 6.0 1.0 3.0 3.0 0 2.0 40.0 95.0 10.0 10.0 10.0 10.0 10.0 9.0 325.0 336.16342457834355 2.0 4 1 37.75964044745488 -122.40942823733772 1 0 4.0 1.0 2.0 2.0 0 2.0 23.0 91.0 9.0 9.0 10.0 10.0 10.0 9.0 225.0 281.5352463757383 2.0 1 1 37.74283330858399 -122.4154299914376 3 0 2.0 1.0 1.0 1.0 0 2.0 25.0 92.0 9.0 9.0 10.0 10.0 10.0 9.0 149.0 169.75953238814026 1.0 1 1 37.74424618748867 -122.41853422693094 0 0 2.0 1.0 0.0 2.0 0 30.0 21.0 99.0 10.0 10.0 10.0 10.0 10.0 10.0 100.0 169.75953238814026 2.0 4 1 37.76097556330237 -122.4215807919612 5 0 4.0 1.0 1.0 2.0 0 1.0 20.0 97.0 10.0 10.0 10.0 10.0 10.0 9.0 199.0 236.9562089196033 4.0 4 1 37.75762488503674 -122.41932566984038 0 1 1.0 1.0 1.0 1.0 0 2.0 83.0 96.0 10.0 9.0 10.0 10.0 10.0 9.0 99.0 121.92584800768144 1.0 1 1 37.74376821969155 -122.41827786422016 0 0 4.0 1.0 2.0 2.0 0 3.0 62.0 96.0 10.0 10.0 10.0 10.0 10.0 9.0 208.0 258.63991704591785 4.0 4 1 37.756526602191336 -122.40921797580076 0 1 1.0 2.0 3.0 1.0 0 1.0 24.0 96.0 10.0 10.0 9.0 10.0 9.0 9.0 69.0 228.94105073267252 1.0 1 1 37.73721650622201 -122.4226450081926 0 0 2.0 1.0 0.0 1.0 0 2.0 18.0 98.0 10.0 10.0 10.0 10.0 9.0 10.0 125.0 169.36297794593742 1.0 4 1 37.75447900325963 -122.42063707492767 0 1 2.0 1.0 1.0 1.0 0 2.0 3.0 93.0 10.0 9.0 10.0 10.0 9.0 10.0 100.0 122.88604398861901 1.0 4 1 37.750905295992936 -122.42327504461153 3 1 2.0 1.0 1.0 1.0 0 2.0 0.0 97.0 10.0 10.0 10.0 10.0 10.0 10.0 99.0 146.24429443070966 3.0 1 1 37.73931982845486 -122.41536911388242 3 1 4.0 1.0 2.0 2.0 0 4.0 8.0 95.0 10.0 10.0 10.0 10.0 10.0 10.0 96.0 248.0041497208078 1.0 1 1 37.73560893377262 -122.41484090436154 1 0 2.0 1.0 1.0 1.0 0 2.0 6.0 100.0 10.0 10.0 10.0 10.0 10.0 10.0 160.0 185.31464233343476 2.0 4 1 37.750175065308675 -122.40468176718477 0 1 1.0 1.0 1.0 1.0 0 3.0 63.0 98.0 10.0 10.0 10.0 10.0 9.0 9.0 90.0 122.88604398861901 1.0 1 1 37.7388292320904 -122.4152943973256 0 0 4.0 1.0 1.0 2.0 0 3.0 73.0 98.0 10.0 10.0 10.0 10.0 10.0 10.0 1

Stop the streams.

In [0]:
[q.stop() for q in spark.streams.active]

Out[24]: [None]

-sandbox
<img alt="Caution" title="Caution" style="vertical-align: text-bottom; position: relative; height:1.3em; top:0.0em" src="https://files.training.databricks.com/static/images/icon-warning.svg"/> **Please be sure to delete any infrastructure you build after the course so you don't incur unexpected expenses.**

<h2><img src="https://files.training.databricks.com/images/105/logo_spark_tiny.png"> All done!</h2>

Thank you for your participation!

-sandbox
&copy; 2021 Databricks, Inc. All rights reserved.<br/>
Apache, Apache Spark, Spark and the Spark logo are trademarks of the <a href="http://www.apache.org/">Apache Software Foundation</a>.<br/>
<br/>
<a href="https://databricks.com/privacy-policy">Privacy Policy</a> | <a href="https://databricks.com/terms-of-use">Terms of Use</a> | <a href="http://help.databricks.com/">Support</a>